# Flowing down the gradient of the map
Given a multivariate polynomial $H(z_1, z_2, \ldots, z_{n-1}, w)$ we numerically solve for the equations which decends the height map $h : \mathcal{V}(H) \to \mathbb{R}^n$.
The implicit function theorem implies the existence of a function $w(z_1, \ldots, z_{n-1}) = w(\vec{z})$ such that $H(\vec{z}, w(\vec{z})) = 0$ in a neighborhood around a point $(\vec{z_0}, w_0)$ such that $H_w(\vec{z_0}, w_0) \neq 0$.
Moreover, the gradient of $w$ is given by
$$\nabla w = - \frac{1}{H_w} (H_{z_1}, \ldots, H_{z_n}).$$

In order to solve for the flow, we first split each variable into real and imaginary parts $\vec{z} \to \vec{x} + i\vec{y}$ and $w \to u + iv$.
Then the partials are given by
$\frac{\partial u}{\partial x_j} = - \Re\left(\frac{H_{z_j}}{H_w}\right)$,
$\frac{\partial v}{\partial x_j} = - \Im\left(\frac{H_{z_j}}{H_w}\right)$,
$\frac{\partial u}{\partial y_j} = - \frac{\partial u}{\partial y_j}$,
$\frac{\partial v}{\partial y_j} = \frac{\partial u}{\partial x_j}$.
Finally we construct the system of differential equations to solve for functions $x_i, y_i, u, v,$ which satisfy
$$\frac{dx_j}{dt} = - \frac{\partial h}{\partial x_j}$$
$$\frac{dy_j}{dt} = - \frac{\partial h}{\partial y_j}$$
where
$$h(\vec{x}, \vec{y}, u, v) = (u^2 + v^2) \prod_{j = 1}^n (x_j^2 + y_j^2).$$
The initial conditions are easily computable and $u', v'$ are given by
$$\frac{du}{dt} = \nabla u \cdot \left( \frac{dx_1}{dt}, \frac{dy_1}{dt}, \ldots, \frac{dx_n}{dt}, \frac{dy_n}{dt} \right)$$
$$\frac{dv}{dt} = \nabla v \cdot \left( \frac{dx_1}{dt}, \frac{dy_1}{dt}, \ldots, \frac{dx_n}{dt}, \frac{dy_n}{dt} \right)$$

In [1]:
using DynamicPolynomials
using DifferentialEquations
using Sundials

In [2]:
# split f(z) into u(x, y) + iv(x, y)
function split(f, z, x, y)
    n = length(z)
    @polyvar I
    f = subs(f, z => x + I*y)
    ℜf = sum(filter(t -> iseven(degree(t, I)), terms(f)))
    ℑf = sum(filter(t -> isodd(degree(t, I)), terms(f)))
    # These polynomials are always real? #TODO: think about that... if it's not true there may be problems...
    return convert(Polynomial{true, Real}, subs(ℜf, I => im)), convert(Polynomial{true, Real}, -im*subs(ℑf, I => im))
end

function split_rational(f, z, x, y)
    n = length(z)
    g = numerator(f)
    h = denominator(f)
    ℜg, ℑg = split(g, z, x, y)
    ℜh, ℑh = split(h, z, x, y)
    
    @polyvar I
    num = (ℜg + I*ℑg) * (ℜh - I*ℑh)
    den = ℜh^2 + ℑh^2
    
    ℜnum = sum(filter(t -> iseven(degree(t, I)), terms(num)))
    ℑnum = sum(filter(t -> isodd(degree(t, I)), terms(num)))
    # Same as above, it will error if it ends up being complex valued.
    return convert(RationalPoly{Polynomial{true, Real}, Polynomial{true, Real}}, subs(ℜnum, I => im) / den), convert(RationalPoly{Polynomial{true, Real}, Polynomial{true, Real}}, -im*subs(ℑnum, I => im) / den)
end

function build_system(H, z, w)
    Hz = differentiate(H, z)
    Hw = differentiate(H, w)
    ∇w = -Hz/Hw
    
    n = length(z)
    @polyvar x[1:n] y[1:n] u v
    ℜH, ℑH = split(H, [z; w], [x; u], [y; v])
    
    split∇w = map(dw -> split_rational(dw, [z; w], [x; u], [y; v]), ∇w)
    dudx = [t[1] for t in split∇w]
    dvdx = [t[2] for t in split∇w]
    dudy = -dvdx
    dvdy = dudx

    dhdx = [2*x[j] * (u^2 + v^2) * prod([x[k]^2 + y[k]^2 for k in 1:n if k != j]) for j in 1:n] + [2*u*dudx[j] + 2*v*dvdx[j] for j in 1:n] .* prod(x.^2 + y.^2) 
    dhdy = [2*y[j] * (u^2 + v^2) * prod([x[k]^2 + y[k]^2 for k in 1:n if k != j]) for j in 1:n] + [2*u*dudy[j] + 2*v*dvdy[j] for j in 1:n] .* prod(x.^2 + y.^2)
    
    dxdt = dhdx
    dydt = dhdy
    dudt = sum([dudx; dudy] .* [dxdt; dydt])
    dvdt = sum([dvdx; dvdy] .* [dxdt; dydt])
    
    function F(out, dz, z, p, t)
        for j in 1:n
            out[j] = convert(Real, dz[j] - dxdt[j]([x; y; u; v] => z))
        end
        for j in 1:n
            out[n+j] = convert(Real, dz[n+j] - dydt[j]([x; y; u; v] => z))
        end
        out[2*n+1] = convert(Real, ℜH([x; y; u; v] => z))
        out[2*n+2] = convert(Real, ℑH([x; y; u; v] => z))
    end
    
    return F, dxdt, dydt, dudt, dvdt, x, y, u, v
    
end

# create a polynomial in n+1 variables for n >= 1
n = 1
@polyvar z[1:n] w
H = 1 - sum(z.^2) - w^2
g(z) = sqrt(1-sum(z.^2)) # this is for initial conditions only (optional)
F, dxdt, dydt, dudt, dvdt, x, y, u, v = build_system(H, z, w)
F
# returns: system, first derivatives as functions of variables x, y, u, v

F (generic function with 1 method)

In [3]:
initial_conditions = []
radius = 1/12
for t in Iterators.product(fill(0:0.28:2π, n)...)
    t = [t[j] for j in 1:n]
    z₀ = radius*exp.(im*t)
    x₀ = real(z₀)
    y₀ = imag(z₀)
    u₀ = real(g(z₀))
    v₀ = imag(g(z₀))
    dx₀ = [dxdt[j]([x; y; u; v] => [x₀; y₀; u₀; v₀]) for j in 1:n]
    dy₀ = [dydt[j]([x; y; u; v] => [x₀; y₀; u₀; v₀]) for j in 1:n]
    du₀ = dudt([x; y; u; v] => [x₀; y₀; u₀; v₀])
    dv₀ = dvdt([x; y; u; v] => [x₀; y₀; u₀; v₀])
    push!(initial_conditions, [[dx₀; dy₀; du₀; dv₀], [x₀; y₀; u₀; v₀]])
end

In [ ]:
tval = 4
tstops = collect(0:0.05:tval)
prob = DAEProblem(F, 
    initial_conditions[1][1], # first order derivatives inititial values
    initial_conditions[1][2], # varible initial values
    tval, tstops=tstops, differential_vars=[ones(Bool, 2*n); zeros(Bool, 2)])
function prob_func(prob, i, repeat)
  remake(prob, du0=initial_conditions[i][1], u0=initial_conditions[i][2])
end

ensemble_prob = EnsembleProblem(prob, prob_func=prob_func)
sim = solve(ensemble_prob, IDA(), EnsembleDistributed(), trajectories=length(initial_conditions))

In [5]:
using Plots
plotly()

# RINGS
rng = 2
N = 200
x = collect(Float16, range(-2, length=N, stop=2))
y = collect(Float16, range(-3, length=N, stop=3))
h(x, y, u, v) = -log(x^2 + y^2)/2 -log(u^2 + v^2)/2
param(x, y) = h(x, y, real(g(x+y*im)), imag(g(x+y*im)))
p = plot(x, y, param, st = :surface, legend = false, axis = true, size=(800,800))

┌ Warning: For saving to png with the `Plotly` backend `PlotlyBase` and `PlotlyKaleido` need to be installed.
│   err =
│    ArgumentError: Package PlotlyKaleido not found in current path.
│    - Run `import Pkg; Pkg.add("PlotlyKaleido")` to install the PlotlyKaleido package.
└ @ Plots ~/.julia/packages/Plots/bMtsB/src/backends.jl:552


In [6]:
ϵ = 1e-14 # close enough to call equal
for i in 1:length(tstops)
    tval = tstops[i]
    if any(isnothing(findfirst(abs.(sol.t .- tval) .< ϵ)) for sol in sim)
        break
    end
    
    # plot ring
    xs = [sol.u[findfirst(abs.(sol.t .- tval) .< ϵ)][1] for sol in sim]
    ys = [sol.u[findfirst(abs.(sol.t .- tval) .< ϵ)][2] for sol in sim]
    us = [sol.u[findfirst(abs.(sol.t .- tval) .< ϵ)][3] for sol in sim]
    vs = [sol.u[findfirst(abs.(sol.t .- tval) .< ϵ)][4] for sol in sim]
    zs = [0.05 + h(xs[idx], ys[idx], us[idx], vs[idx]) for idx in 1:length(sim)]
    plot!(xs, ys, zs, lc = RGB(0.1, 1 - (i+1)/length(tstops), 0.8), lw = 5)
end

p